In [1]:
# Impor library yang diperlukan
from pyspark.sql import SparkSession
from pyspark.sql.functions import from_json, col, expr, when, to_timestamp
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DoubleType

In [2]:
# Membuat SparkSession
spark = SparkSession.builder \
    .appName("PredictiveMaintenanceStreaming") \
    .master("spark://spark-master:7077") \
    .config("spark.jars.packages", "org.apache.spark:spark-sql-kafka-0-10_2.12:3.3.0") \
    .getOrCreate()

print("SparkSession berhasil dibuat.")

:: loading settings :: url = jar:file:/opt/conda/lib/python3.11/site-packages/pyspark/jars/ivy-2.5.0.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /home/jovyan/.ivy2/cache
The jars for the packages stored in: /home/jovyan/.ivy2/jars
org.apache.spark#spark-sql-kafka-0-10_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-106791d7-7bd8-49fd-8bea-484db9dd2419;1.0
	confs: [default]
	found org.apache.spark#spark-sql-kafka-0-10_2.12;3.3.0 in central
	found org.apache.spark#spark-token-provider-kafka-0-10_2.12;3.3.0 in central
	found org.apache.kafka#kafka-clients;2.8.1 in central
	found org.lz4#lz4-java;1.8.0 in central
	found org.xerial.snappy#snappy-java;1.1.8.4 in central
	found org.slf4j#slf4j-api;1.7.32 in central
	found org.apache.hadoop#hadoop-client-runtime;3.3.2 in central
	found org.spark-project.spark#unused;1.0.0 in central
	found org.apache.hadoop#hadoop-client-api;3.3.2 in central
	found commons-logging#commons-logging;1.1.3 in central
	found com.google.code.findbugs#jsr305;3.0.0 in central
	found org.apache.commons#commons-pool2;2.11.1 in central
downloa

25/07/15 15:15:06 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


SparkSession berhasil dibuat.


In [3]:
# Mendefinisikan Skema
raw_schema = StructType([
    StructField("timestamp", StringType(), True),
    StructField("machine_id", StringType(), True),
    StructField("vibration", DoubleType(), True),
    StructField("acoustic", DoubleType(), True),
    StructField("temperature", DoubleType(), True),
    StructField("current", DoubleType(), True),
    StructField("IMF_1", DoubleType(), True),
    StructField("IMF_2", DoubleType(), True),
    StructField("IMF_3", DoubleType(), True),
    StructField("label", IntegerType(), True)
])

In [4]:
# Membaca dari topik Kafka
raw_stream_df = spark \
    .readStream \
    .format("kafka") \
    .option("kafka.bootstrap.servers", "kafka:9092") \
    .option("subscribe", "raw_sensor_data") \
    .option("startingOffsets", "earliest") \
    .load()

In [5]:
raw_stream_df.printSchema()

root
 |-- key: binary (nullable = true)
 |-- value: binary (nullable = true)
 |-- topic: string (nullable = true)
 |-- partition: integer (nullable = true)
 |-- offset: long (nullable = true)
 |-- timestamp: timestamp (nullable = true)
 |-- timestampType: integer (nullable = true)



In [6]:
# Parsing dan Transformasi Data
parsed_df = raw_stream_df \
    .select(from_json(col("value").cast("string"), raw_schema).alias("data")) \
    .select("data.*")

In [7]:
# Transformasi utama
# transformed_df = parsed_df \
#     .withColumn("event_timestamp", to_timestamp(col("datetime"))) \
#     .withColumn("status",
#         when((col("volt") > 250) | (col("volt") < 190), "Voltage Anomaly")
#         .when(col("vibration") > 70, "High Vibration")
#         .otherwise("Normal")
#     )

In [7]:
transformed_df = parsed_df \
    .withColumn("event_timestamp", to_timestamp(col("timestamp"))) \
    .withColumn("status",
        when(col("label") == 1, "Failure Detected")
        .otherwise("Normal")
    )

In [8]:
# Pilih kolom final
final_df = transformed_df.select(
    "event_timestamp", "machine_id", "vibration", "acoustic", 
    "temperature", "current", "status",
    "IMF_1", "IMF_2", "IMF_3",
    "label"
)

In [9]:
# Memastikan transformasi benar sebelum menulis kembali ke Kafka.
# Menulis ke konsol untuk debugging
console_query = final_df \
    .writeStream \
    .outputMode("append") \
    .format("console") \
    .option("truncate", "false") \
    .start()

25/07/15 15:15:44 WARN ResolveWriteToStream: Temporary checkpoint location created which is deleted normally when the query didn't fail: /tmp/temporary-aff9ad49-7183-4dd1-a731-2a049fb2fda7. If it's required to delete it under any circumstances, please set spark.sql.streaming.forceDeleteTempCheckpointLocation to true. Important to know deleting temp checkpoint folder is best effort.
25/07/15 15:15:44 WARN ResolveWriteToStream: spark.sql.adaptive.enabled is not supported in streaming DataFrames/Datasets and will be disabled.


In [10]:
# Menulis ke topik Kafka yang sudah bersih
kafka_output_df = final_df.select(expr("to_json(struct(*)) AS value"))
kafka_query = kafka_output_df \
    .writeStream \
    .format("kafka") \
    .option("kafka.bootstrap.servers", "kafka:9092") \
    .option("topic", "clean_sensor_data") \
    .option("checkpointLocation", "/tmp/spark_checkpoints/kafka_sensor_writer") \
    .start()

25/07/15 15:15:45 WARN ResolveWriteToStream: spark.sql.adaptive.enabled is not supported in streaming DataFrames/Datasets and will be disabled.
25/07/15 15:15:47 WARN NetworkClient: [Consumer clientId=consumer-spark-kafka-source-97702a23-3510-4aaa-8675-d8340532442f--1462910457-driver-0-1, groupId=spark-kafka-source-97702a23-3510-4aaa-8675-d8340532442f--1462910457-driver-0] Error while fetching metadata with correlation id 2 : {raw_sensor_data=UNKNOWN_TOPIC_OR_PARTITION}
25/07/15 15:15:47 WARN NetworkClient: [Consumer clientId=consumer-spark-kafka-source-97702a23-3510-4aaa-8675-d8340532442f--1462910457-driver-0-1, groupId=spark-kafka-source-97702a23-3510-4aaa-8675-d8340532442f--1462910457-driver-0] Error while fetching metadata with correlation id 4 : {raw_sensor_data=UNKNOWN_TOPIC_OR_PARTITION}
25/07/15 15:15:47 WARN NetworkClient: [Consumer clientId=consumer-spark-kafka-source-97702a23-3510-4aaa-8675-d8340532442f--1462910457-driver-0-1, groupId=spark-kafka-source-97702a23-3510-4aaa-86

-------------------------------------------
Batch: 0
-------------------------------------------
+---------------+----------+---------+--------+-----------+-------+------+-----+-----+-----+-----+
|event_timestamp|machine_id|vibration|acoustic|temperature|current|status|IMF_1|IMF_2|IMF_3|label|
+---------------+----------+---------+--------+-----------+-------+------+-----+-----+-----+-----+
+---------------+----------+---------+--------+-----------+-------+------+-----+-----+-----+-----+



-------------------------------------------
Batch: 1
-------------------------------------------


+-------------------+----------+---------+--------+-----------+-------+------+-----+-----+-----+-----+
|event_timestamp    |machine_id|vibration|acoustic|temperature|current|status|IMF_1|IMF_2|IMF_3|label|
+-------------------+----------+---------+--------+-----------+-------+------+-----+-----+-----+-----+
|2024-07-01 08:00:00|M01       |0.822    |0.645   |66.85      |13.04  |Normal|0.196|0.033|0.0  |0    |
+-------------------+----------+---------+--------+-----------+-------+------+-----+-----+-----+-----+



-------------------------------------------
Batch: 2
-------------------------------------------


...

-------------------------------------------
Batch: 280
-------------------------------------------
+-------------------+----------+---------+--------+-----------+-------+----------------+-----+------+------+-----+
|event_timestamp    |machine_id|vibration|acoustic|temperature|current|status          |IMF_1|IMF_2 |IMF_3 |label|
+-------------------+----------+---------+--------+-----------+-------+----------------+-----+------+------+-----+
|2024-07-01 12:40:00|M01       |0.878    |0.671   |63.66      |12.04  |Normal          |0.114|-0.025|-0.032|0    |
|null               |M01       |0.766    |0.572   |67.05      |11.88  |Normal          |0.177|0.057 |-0.033|0    |
|null               |M01       |0.725    |0.545   |64.63      |12.44  |Normal          |0.127|-0.061|-0.036|0    |
|null               |M01       |0.869    |0.631   |65.14      |12.03  |Normal          |0.259|0.013 |-0.037|0    |
|null               |M01       |0.749    |0.574   |68.58      |11.53  |Normal          |0.176|0.

-------------------------------------------
Batch: 672
-------------------------------------------
+---------------+----------+---------+--------+-----------+-------+----------------+-----+------+-----+-----+
|event_timestamp|machine_id|vibration|acoustic|temperature|current|status          |IMF_1|IMF_2 |IMF_3|label|
+---------------+----------+---------+--------+-----------+-------+----------------+-----+------+-----+-----+
|null           |M01       |1.227    |0.923   |80.72      |16.7   |Failure Detected|0.147|0.011 |0.05 |1    |
|null           |M01       |0.788    |0.536   |63.69      |13.17  |Normal          |0.136|0.033 |0.05 |0    |
|null           |M01       |0.713    |0.591   |69.08      |12.33  |Normal          |0.154|-0.001|0.05 |0    |
|null           |M01       |0.776    |0.506   |67.29      |11.05  |Normal          |0.139|0.084 |0.05 |0    |
|null           |M01       |0.83     |0.622   |60.65      |11.68  |Normal          |0.123|-0.01 |0.05 |0    |
|null           |M01 

-------------------------------------------
Batch: 677
-------------------------------------------


+---------------+----------+---------+--------+-----------+-------+----------------+-----+------+------+-----+
|event_timestamp|machine_id|vibration|acoustic|temperature|current|status          |IMF_1|IMF_2 |IMF_3 |label|
+---------------+----------+---------+--------+-----------+-------+----------------+-----+------+------+-----+
|null           |M01       |0.767    |0.549   |67.12      |11.99  |Normal          |0.226|0.001 |-0.021|0    |
|null           |M01       |1.105    |0.915   |81.21      |15.58  |Failure Detected|0.117|-0.166|-0.019|1    |
|null           |M01       |0.795    |0.638   |63.41      |11.98  |Normal          |0.197|-0.009|-0.018|0    |
|null           |M01       |0.829    |0.667   |65.47      |12.11  |Normal          |0.183|-0.047|-0.016|0    |
|null           |M01       |0.8      |0.567   |62.37      |12.87  |Normal          |0.13 |0.01  |-0.012|0    |
|null           |M01       |1.35     |1.027   |78.45      |14.41  |Failure Detected|0.251|0.168 |-0.011|1    |
|

-------------------------------------------
Batch: 1446
-------------------------------------------
+---------------+----------+---------+--------+-----------+-------+----------------+-----+------+-----+-----+
|event_timestamp|machine_id|vibration|acoustic|temperature|current|status          |IMF_1|IMF_2 |IMF_3|label|
+---------------+----------+---------+--------+-----------+-------+----------------+-----+------+-----+-----+
|null           |M01       |1.227    |0.923   |80.72      |16.7   |Failure Detected|0.147|0.011 |0.05 |1    |
|null           |M01       |0.788    |0.536   |63.69      |13.17  |Normal          |0.136|0.033 |0.05 |0    |
|null           |M01       |0.713    |0.591   |69.08      |12.33  |Normal          |0.154|-0.001|0.05 |0    |
|null           |M01       |0.776    |0.506   |67.29      |11.05  |Normal          |0.139|0.084 |0.05 |0    |
|null           |M01       |0.83     |0.622   |60.65      |11.68  |Normal          |0.123|-0.01 |0.05 |0    |
|null           |M01

In [ ]:
# Untuk menghentikan semua query:
console_query.stop()
kafka_query.stop()